Stages getting data:
1. pull new data from hopkins repo
2. run this file
3. save as hopkins_conf_gf\<timestamp\> pickle
4. add GDP, urb, democracy, GINI and tests and save as hopkins_conf_GDP_URB\<timestamp\> pickle
5. run add_death_data and save as hopkins_death_augmented_GDP_URB\<timestamp\> pickle
6. Compute GF and 5%date for both files and save as hopkins_\<death\conf\>_GDP_URB_GF_\<timestamp\> pickle
7. compute avg_intervals and save pickle again in data_analysis
7. Remove nans and make sure no place below 20 for conf and 2 for death in data_analysis

Stages updating data:
* updating data will not show new locations where n > 20

In [ ]:
import urllib
import json
import pandas as pd
import numpy as np
import warnings
import pickle
from datetime import datetime
from datetime import timedelta
from urllib.error import URLError
from functools import wraps
from keys import client_id, client_secret, app_id
warnings.filterwarnings('ignore')

In [2]:
DIAMOND_PRINCESS_COORD = (35.4437, 139.638)
BARBADOS_BELIZE_COORD = (13.1939, -59.5432)
CONGO_BRAZZAVILLE_KINSHASA_COORD = (-4.0383, 21.7587)
MASSACHUSETTS_COORD = (41.40674725, -70.68763497)
RADIUS = 350 # Miles
TIMEOUT = 10 # Seconds
LOG_PATH = 'weather_logs/'
GLOBAL_PATH = '../original_datasets/remote_repo/csse_covid_19_data/csse_covid_19_time_series/'\
              'time_series_covid19_confirmed_global.csv'
US_PATH = '../original_datasets/remote_repo/csse_covid_19_data/csse_covid_19_time_series/'\
          'time_series_covid19_confirmed_US.csv'

In [3]:
# Decorator function for timeout handling
def try_three_times(func):
    @wraps(func)
    def decoration_func(*args,**kwargs):
        for i in range(3):
            try:
                return func(*args,**kwargs)
            except Exception as e:
                if i == 2:
                    raise
    return decoration_func

@try_three_times
def request_url(url, timeout=10):
     return urllib.request.urlopen(url, timeout=timeout)

###### Load datasets
Notes on data: 
1. Notice that some of the dates on the hopkins dataset appear in different format in ecxel, they are infect all in the same format: %-m/%-d/20
2. Column names are modifyed to %-m/%-d/20 to fit weather API queries
3. All three rows reffering to 'Diamnond princess' have been removed
4. The location (0,0) has been removed
5. Two places with the same coordinate have been slightly modified to accomedate indexing
4. source: https://github.com/CSSEGISandData/COVID-19/tree/master/csse_covid_19_data/csse_covid_19_time_series

In [204]:
global_df = pd.read_csv(GLOBAL_PATH)
us_df = pd.read_csv(US_PATH)
us_df.drop(columns=['UID', 'iso2', 'iso3', 'code3', 'FIPS', 'Admin2', 'Combined_Key'], inplace=True)
us_df.rename(columns={'Long_': 'Long'}, inplace=True)
global_df.rename(columns={'Country/Region': 'Country_Region',\
                                                  'Province/State': 'Province_State'}, inplace=True)
hopkins_confirmed = pd.concat([global_df, us_df])

# This is a very ugly fix to remove duplicates from Utah that spoil the multiindex 
# These indexes should be updated every time a new df is loaded
idx = [2805, 2809, 2782, 2783, 2784, 2785, 2786, 2788, 2789,\
       2790, 2791, 2792, 2793, 2794, 2795, 2796, 2797, 2798,\
       2800, 2801, 2802, 3255, 3256, 3257, 3258, 3259, 3260]
for ind in idx:
    hopkins_confirmed.drop(index=ind, inplace=True)

# Concating the two tables creates dups in index
# This has to be run after the Utah fix
hopkins_confirmed.reset_index(inplace=True)

hopkins_confirmed.drop(hopkins_confirmed[hopkins_confirmed['Lat']\
                                             == DIAMOND_PRINCESS_COORD[0]].index, inplace=True)

hopkins_confirmed.drop(hopkins_confirmed[hopkins_confirmed['Lat']\
                                             == MASSACHUSETTS_COORD[0]].index, inplace=True)

hopkins_confirmed.loc[hopkins_confirmed['Country_Region']=='Barbados', 'Lat']\
                        = BARBADOS_BELIZE_COORD[0] + 0.00001

hopkins_confirmed.loc[hopkins_confirmed['Country_Region']=='Congo (Brazzaville)', 'Lat']\
                        = CONGO_BRAZZAVILLE_KINSHASA_COORD[0] + 0.00001

hopkins_confirmed.drop(hopkins_confirmed.loc[hopkins_confirmed['Lat'] == 0].index, inplace=True)

In [206]:
len(hopkins_confirmed)
to_drop = []
for i in hopkins_confirmed.index:
    if hopkins_confirmed.loc[i].iloc[5:].max() < 20:
        to_drop.append(i)
        
hopkins_confirmed.drop(index=to_drop, inplace=True)
len(hopkins_confirmed)

3388

1839

###### Setup multi-index

In [207]:
coords = [x for x in zip(hopkins_confirmed.pop('Lat'), hopkins_confirmed.pop('Long'))]
hopkins_confirmed.index = coords

for param in ['avg_m_wind', 'avg_m_precip', 'avg_m_RH', 'avg_m_tmp',]:
    hopkins_confirmed.insert(2, param, np.nan)
hopkins_confirmed.insert(6, 'weather', '')

columns = len(hopkins_confirmed.columns)

for index in hopkins_confirmed.index:
    for param in ['avg_d_tmp', 'avg_d_RH', 'avg_d_wind', 'avg_d_precip']:
        hopkins_confirmed = hopkins_confirmed.append\
                (pd.Series([np.nan]*6+[param]+[np.nan]*(columns-7), index=hopkins_confirmed.columns, name=index))

hopkins_confirmed.set_index('weather', append=True, inplace=True)
hopkins_confirmed = hopkins_confirmed.sort_index()
dates = {date: date + '20' for date in hopkins_confirmed.columns[6:]}
hopkins_confirmed = hopkins_confirmed.rename(columns=dates)

In [208]:
hopkins_confirmed.rename(index={'': 'data'}, inplace=True)
hopkins_confirmed.rename_axis(['coordinate', 'information'],inplace=True)
for param in ['Max_Cases', 'GF_Q1', 'GF_Q2', 'GF_Q3'][::-1]:
    hopkins_confirmed.insert(6, param, np.nan)

In [211]:
hopkins_confirmed

index Province_State  avg_m_tmp  avg_m_RH  \
coordinate           information                                               
(-41.4545, 145.9707) data           13.0       Tasmania        NaN       NaN   
                     avg_d_RH        NaN            NaN        NaN       NaN   
                     avg_d_precip    NaN            NaN        NaN       NaN   
                     avg_d_tmp       NaN            NaN        NaN       NaN   
                     avg_d_wind      NaN            NaN        NaN       NaN   
...                                  ...            ...        ...       ...   
(64.9631, -19.0208)  data          130.0            NaN        NaN       NaN   
                     avg_d_RH        NaN            NaN        NaN       NaN   
                     avg_d_precip    NaN            NaN        NaN       NaN   
                     avg_d_tmp       NaN            NaN        NaN       NaN   
                     avg_d_wind      NaN            NaN        NaN       NaN   

                                   avg_m_precip  avg_m_wind  Max_Cases  GF_Q1  \
coordinate           information                                                
(-41.4545, 145.9707) data                   NaN         NaN        NaN    NaN   
                     avg_d_RH               NaN         NaN        NaN    NaN   
                     avg_d_precip           NaN         NaN        NaN    NaN   
                     avg_d_tmp              NaN         NaN        NaN    NaN   
                     avg_d_wind             NaN         NaN        NaN    NaN   
...                                         ...         ...        ...    ...   
(64.9631, -19.0208)  data                   NaN         NaN        NaN    NaN   
                     avg_d_RH               NaN         NaN        NaN    NaN   
                     avg_d_precip           NaN         NaN        NaN    NaN   
                     avg_d_tmp              NaN         NaN        NaN    NaN   
                     avg_d_wind             NaN         NaN        NaN    NaN   

                                   GF_Q2  GF_Q3  ... 4/27/2020  4/28/2020  \
coordinate           information                 ...                        
(-41.4545, 145.9707) data            NaN    NaN  ...     214.0      218.0   
                     avg_d_RH        NaN    NaN  ...       NaN        NaN   
                     avg_d_precip    NaN    NaN  ...       NaN        NaN   
                     avg_d_tmp       NaN    NaN  ...       NaN        NaN   
                     avg_d_wind      NaN    NaN  ...       NaN        NaN   
...                                  ...    ...  ...       ...        ...   
(64.9631, -19.0208)  data            NaN    NaN  ...    1792.0     1795.0   
                     avg_d_RH        NaN    NaN  ...       NaN        NaN   
                     avg_d_precip    NaN    NaN  ...       NaN        NaN   
                     avg_d_tmp       NaN    NaN  ...       NaN        NaN   
                     avg_d_wind      NaN    NaN  ...       NaN        NaN   

                                   4/29/2020  4/30/2020  5/1/2020  5/2/2020  \
coordinate           information                                              
(-41.4545, 145.9707) data              219.0      221.0     221.0     221.0   
                     avg_d_RH            NaN        NaN       NaN       NaN   
                     avg_d_precip        NaN        NaN       NaN       NaN   
                     avg_d_tmp           NaN        NaN       NaN       NaN   
                     avg_d_wind          NaN        NaN       NaN       NaN   
...                                      ...        ...       ...       ...   
(64.9631, -19.0208)  data             1797.0     1797.0    1798.0    1798.0   
                     avg_d_RH            NaN        NaN       NaN       NaN   
                     avg_d_precip        NaN        NaN       NaN       NaN   
                     avg_d_tmp           NaN        NaN       NaN    

###### Query remote database

In [64]:
INTERVAL = 7

days = hopkins_confirmed.columns[10:].tolist()
q = 0
log = open('{0}log{1}.txt'.format(LOG_PATH, datetime.now().strftime('%d%m%Y')), 'w')

# Patching tools:
# coords = list(set(hopkins_confirmed.index.get_level_values(0).tolist()))
# days = days[:12]
# coords = coords[2851:]
# q = 2851

while days:
    start_time = days[0]
    end_time = days[:INTERVAL][-1]
    days = days[INTERVAL:]
    for coord in coords:
        q += 1
        lat = coord[0]
        long = coord[1]
        country = hopkins_confirmed.loc[coord]['Country_Region'].values[0]
        province = hopkins_confirmed.loc[coord]['Province_State'].values[0]
        url = 'https://api.aerisapi.com/observations/summary/closest?p={0},{1}&from={2}&to={3}&radius={4}miles&plimit=31&limit=1&'\
              'client_id={5}&client_secret={6}'.format(lat, long, start_time, end_time, RADIUS, client_id, client_secret)
        msg = 'collecting for {0} location {1}, {2} from {3} to {4}\n{5}'\
        .format(q, province, country, start_time, end_time, url)
        _ = log.write('\n' + msg)
        print(msg)
        try:
            request = request_url(url, TIMEOUT)
            response = request.read()
            json_ = json.loads(response)
        except URLError as e:
            msg = 'Tried three times, moving forward\n'
            print(msg)
            _ = log.write(msg)
            continue
        if json_['success']: 
            _ = log.write('\nsuccess')
            print('success')
            try:
                for day in json_['response'][0]['periods']:
                    date = datetime.strptime(str(day['summary']['ymd']), '%Y%m%d').strftime("%-m/%-d/%Y")
                    hopkins_confirmed.loc[coord].at['avg_d_tmp', date] = day['summary']['temp']['avgC']
                    hopkins_confirmed.loc[coord].at['avg_d_RH', date] = day['summary']['rh']['avg']
                    hopkins_confirmed.loc[coord].at['avg_d_wind', date] = day['summary']['wind']['avgKPH']
                    hopkins_confirmed.loc[coord].at['avg_d_precip', date] = day['summary']['precip']['totalMM']
            except IndexError:
                if json_['error']:
                    msg = 'No data found for {0}, {1} at {2}\n{3}\r\n'.format(country, province, date, json_['error'])
                    _ = log.write(msg)
                    print(msg)
            except Exception:
                msg = 'Unknowen error\n{0}\r\n'.format(json_['error'])
                _ = log.write(msg)
                print(msg)
            finally:
                request.close()
        else:
            print('Failed')
            _ = log.write('Failed')
log.close()

collecting for 1 location nan, Afghanistan from 1/22/2020 to 2/2/2020
https://api.aerisapi.com/observations/summary/closest?p=33.0,65.0&from=1/22/2020&to=2/2/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 2 location nan, Albania from 1/22/2020 to 2/2/2020
https://api.aerisapi.com/observations/summary/closest?p=41.1533,20.1683&from=1/22/2020&to=2/2/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 3 location nan, Algeria from 1/22/2020 to 2/2/2020
https://api.aerisapi.com/observations/summary/closest?p=28.0339,1.6596&from=1/22/2020&to=2/2/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 4 location nan, Andorra from 1/22/2020 to 2/2/2020
https://api.aerisapi.com/observations/summary/closest?p

success
collecting for 29 location nan, Brunei from 1/22/2020 to 2/2/2020
https://api.aerisapi.com/observations/summary/closest?p=4.5353,114.7277&from=1/22/2020&to=2/2/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 30 location nan, Bulgaria from 1/22/2020 to 2/2/2020
https://api.aerisapi.com/observations/summary/closest?p=42.7339,25.4858&from=1/22/2020&to=2/2/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 31 location nan, Burkina Faso from 1/22/2020 to 2/2/2020
https://api.aerisapi.com/observations/summary/closest?p=12.2383,-1.5616&from=1/22/2020&to=2/2/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 32 location nan, Cabo Verde from 1/22/2020 to 2/2/2020
https://api.aerisapi.com/observa

success
collecting for 57 location Hebei, China from 1/22/2020 to 2/2/2020
https://api.aerisapi.com/observations/summary/closest?p=39.549,116.1306&from=1/22/2020&to=2/2/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 58 location Heilongjiang, China from 1/22/2020 to 2/2/2020
https://api.aerisapi.com/observations/summary/closest?p=47.862,127.7615&from=1/22/2020&to=2/2/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 59 location Henan, China from 1/22/2020 to 2/2/2020
https://api.aerisapi.com/observations/summary/closest?p=33.882,113.614&from=1/22/2020&to=2/2/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 60 location Hong Kong, China from 1/22/2020 to 2/2/2020
https://api.aerisapi.com/obser

success
collecting for 85 location nan, Cuba from 1/22/2020 to 2/2/2020
https://api.aerisapi.com/observations/summary/closest?p=22.0,-80.0&from=1/22/2020&to=2/2/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 86 location nan, Cyprus from 1/22/2020 to 2/2/2020
https://api.aerisapi.com/observations/summary/closest?p=35.1264,33.4299&from=1/22/2020&to=2/2/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 87 location nan, Czechia from 1/22/2020 to 2/2/2020
https://api.aerisapi.com/observations/summary/closest?p=49.8175,15.473&from=1/22/2020&to=2/2/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 88 location Greenland, Denmark from 1/22/2020 to 2/2/2020
https://api.aerisapi.com/observations/summar

success
collecting for 113 location nan, Greece from 1/22/2020 to 2/2/2020
https://api.aerisapi.com/observations/summary/closest?p=39.0742,21.8243&from=1/22/2020&to=2/2/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 114 location nan, Guatemala from 1/22/2020 to 2/2/2020
https://api.aerisapi.com/observations/summary/closest?p=15.7835,-90.2308&from=1/22/2020&to=2/2/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 115 location nan, Guinea from 1/22/2020 to 2/2/2020
https://api.aerisapi.com/observations/summary/closest?p=9.9456,-9.6966&from=1/22/2020&to=2/2/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 116 location nan, Guyana from 1/22/2020 to 2/2/2020
https://api.aerisapi.com/observations

...

success
collecting for 17393 location Virginia, US from 4/27/2020 to 5/6/2020
https://api.aerisapi.com/observations/summary/closest?p=38.61807452,-78.48797204&from=4/27/2020&to=5/6/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 17394 location Virginia, US from 4/27/2020 to 5/6/2020
https://api.aerisapi.com/observations/summary/closest?p=36.6801638,-80.2865648&from=4/27/2020&to=5/6/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 17395 location Virginia, US from 4/27/2020 to 5/6/2020
https://api.aerisapi.com/observations/summary/closest?p=37.55016038,-77.91267882&from=4/27/2020&to=5/6/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 17396 location Virginia, US from 4/27/2020 to 5/6/2020
htt

success
collecting for 17420 location Washington, US from 4/27/2020 to 5/6/2020
https://api.aerisapi.com/observations/summary/closest?p=48.471143100000006,-118.5154041&from=4/27/2020&to=5/6/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 17421 location Washington, US from 4/27/2020 to 5/6/2020
https://api.aerisapi.com/observations/summary/closest?p=46.53351425,-118.9018212&from=4/27/2020&to=5/6/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 17422 location Washington, US from 4/27/2020 to 5/6/2020
https://api.aerisapi.com/observations/summary/closest?p=47.14003705,-123.7820567&from=4/27/2020&to=5/6/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 17423 location Washington, US from 4/27/202

success
collecting for 17447 location West Virginia, US from 4/27/2020 to 5/6/2020
https://api.aerisapi.com/observations/summary/closest?p=37.65390597,-80.86009693&from=4/27/2020&to=5/6/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 17448 location West Virginia, US from 4/27/2020 to 5/6/2020
https://api.aerisapi.com/observations/summary/closest?p=39.33602617,-80.0421439&from=4/27/2020&to=5/6/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 17449 location West Virginia, US from 4/27/2020 to 5/6/2020
https://api.aerisapi.com/observations/summary/closest?p=39.11240885,-79.57053576&from=4/27/2020&to=5/6/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 17450 location West Virginia, US from 4/27

success
collecting for 17474 location Wisconsin, US from 4/27/2020 to 5/6/2020
https://api.aerisapi.com/observations/summary/closest?p=45.38553432,-88.03324599999998&from=4/27/2020&to=5/6/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 17475 location Wisconsin, US from 4/27/2020 to 5/6/2020
https://api.aerisapi.com/observations/summary/closest?p=43.81911946,-89.40073763&from=4/27/2020&to=5/6/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 17476 location Wisconsin, US from 4/27/2020 to 5/6/2020
https://api.aerisapi.com/observations/summary/closest?p=43.00486062,-87.96733172&from=4/27/2020&to=5/6/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 17477 location Wisconsin, US from 4/27/2020 to 

success
collecting for 17501 location Wyoming, US from 4/27/2020 to 5/6/2020
https://api.aerisapi.com/observations/summary/closest?p=41.65943896,-108.8827882&from=4/27/2020&to=5/6/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 17502 location Wyoming, US from 4/27/2020 to 5/6/2020
https://api.aerisapi.com/observations/summary/closest?p=41.2878183,-110.54757820000002&from=4/27/2020&to=5/6/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 17503 location Wyoming, US from 4/27/2020 to 5/6/2020
https://api.aerisapi.com/observations/summary/closest?p=43.90451606,-107.68018700000002&from=4/27/2020&to=5/6/2020&radius=350miles&plimit=31&limit=1&client_id=tXyXXyb3Yf492X1asICz5&client_secret=WJi1enKSDGlhO8Nt4Ze00C1F6LEdMpl2O54JIwaM
success
collecting for 17504 location Wyoming, US from 4/27/2020 to 5

###### Verify integrity, handle NaN and backup dataframe
1. Some coordinates are more then 350 miles away from any weather station, resulting in NaN values
2. Some stations don't save data as far back, resulting in NaN values
3. NaNs are not removed, rather when applying aggragate functions we discard then in the calculations

In [135]:
backup1 = hopkins_confirmed.copy()
# data[['Province_State']] = data[['Province_State']].fillna(0)
# confirmed_time_data = confirmed_time_data.dropna()
# confirmed_time_data.isna().sum()
# confirmed_time_data['1/22/2020']
hopkins_confirmed[hopkins_confirmed.columns[10:]].isnull().sum()
sorted(hopkins_confirmed[hopkins_confirmed.columns[10:]].isnull().sum())
hopkins_confirmed[hopkins_confirmed.columns[10:]].isnull().sum().max()

1/22/2020     85
1/23/2020    157
1/24/2020    201
1/25/2020    291
1/26/2020    398
            ... 
5/2/2020      37
5/3/2020      45
5/4/2020      53
5/5/2020      50
5/6/2020      57
Length: 106, dtype: int64

[28,
 28,
 30,
 35,
 37,
 37,
 39,
 39,
 43,
 44,
 45,
 45,
 47,
 47,
 49,
 50,
 51,
 51,
 53,
 55,
 55,
 56,
 57,
 57,
 57,
 58,
 60,
 61,
 61,
 64,
 66,
 66,
 67,
 68,
 72,
 74,
 75,
 76,
 78,
 81,
 83,
 84,
 85,
 86,
 89,
 90,
 90,
 90,
 92,
 92,
 93,
 96,
 97,
 99,
 100,
 100,
 102,
 102,
 103,
 104,
 107,
 107,
 107,
 110,
 111,
 111,
 111,
 112,
 115,
 120,
 122,
 126,
 127,
 128,
 128,
 135,
 137,
 138,
 141,
 152,
 157,
 167,
 167,
 174,
 179,
 183,
 186,
 186,
 188,
 197,
 201,
 211,
 225,
 291,
 315,
 364,
 380,
 398,
 413,
 474,
 487,
 508,
 517,
 555,
 577,
 593]

593

###### COMPUTE AVG PARAMETERS FOR CONFIRMED CASES

In [162]:
means = hopkins_confirmed.mean(axis=1, skipna=True)
i=0
for coord in coords:
    hopkins_confirmed.loc[coord]['avg_m_tmp'].loc['data'] = means.loc[coord]['avg_d_tmp']
    hopkins_confirmed.loc[coord]['avg_m_RH'].loc['data'] = means.loc[coord]['avg_d_RH']
    hopkins_confirmed.loc[coord]['avg_m_wind'].loc['data'] = means.loc[coord]['avg_d_wind']
    hopkins_confirmed.loc[coord]['avg_m_precip'].loc['data'] = means.loc[coord]['avg_d_precip']
    print(i)
    i += 1

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

1862
1863
1864
1865
1866
1867
1868
1869
1870
1871
1872
1873
1874
1875
1876
1877
1878
1879
1880
1881
1882
1883
1884
1885
1886
1887
1888
1889
1890
1891
1892
1893
1894
1895
1896
1897
1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
1928
1929
1930
1931
1932
1933
1934
1935
1936
1937
1938
1939
1940
1941
1942


In [166]:
hopkins_confirmed[hopkins_confirmed['Province_State'] == 'Alaska']


1945.0

###### Data validation, NaN handling
We can spot places where data is currupt if thier average is null, we remove them:

In [84]:
hopkins_confirmed['avg_m_tmp'][::5].isna().sum()
hopkins_confirmed['avg_m_RH'][::5].isna().sum()
hopkins_confirmed['avg_m_wind'][::5].isna().sum()
hopkins_confirmed['avg_m_precip'][::5].isna().sum()

# We run this until there are 0 in all nulls
nulls = hopkins_confirmed['avg_m_wind'][::5].isna().tolist()
for i in range(len(nulls)):
    if nulls[i]:
        nc = hopkins_confirmed['avg_m_precip'][::5].index[i][0]
        print('Removing null at coor {0}, {1}'.format(nc, hopkins_confirmed.loc[nc, 'Country_Region']))
        hopkins_confirmed.drop(nc, level=0, inplace=True)
        for i in range(len(coords)):
            if coords[i] == nc:
                coords.pop(i)
                i += 1

0

0

0

0

###### Compute max cases and max date

In [85]:
backup2 = hopkins_confirmed.copy()
hopkins_confirmed.insert(7, '5%_Date', '')
hopkins_confirmed.insert(7, 'Max_Date', '')

In [138]:
hopkins_confirmed.index.levels[0]

Index([       (-51.7963, -59.5236),        (-41.4545, 145.9707),
              (-38.4161, -63.6167),        (-37.8136, 144.9631),
               (-35.6751, -71.543),        (-35.4735, 149.0124),
              (-34.9285, 138.6007),        (-33.8688, 151.2093),
              (-32.5228, -55.7658),        (-31.9505, 115.8605),
       ...
       (63.87692095, -143.2127643),                (64.0, 26.0),
       (64.80726247, -146.5692662),        (64.8255, -124.8457),
       (64.90320724, -164.0353804),         (64.9631, -19.0208),
       (65.50815459, -151.3907387), (67.04919196, -159.7503946),
       (69.31479216, -153.4836093),         (71.7069, -42.6043)],
      dtype='object', name='coordinate', length=1945)

In [94]:
for coord in coords:
    try:
        max_cases = hopkins_confirmed.iloc[:,12:].loc[coord].loc['data'].max()
        date_pointer = hopkins_confirmed.iloc[:,12:].loc[coord].loc['data'].argmax() 
        max_date = hopkins_confirmed.columns[date_pointer + 12]
#         max_date_index = hopkins_death.iloc[:,12:].loc[coord].loc['data'].argmax()
#         max_date = hopkins_death.iloc[:,12:].loc[coord].loc['data'].index[max_date_index]
        hopkins_confirmed.loc[coord, 'Max_Cases'].loc['data'] = max_cases
        hopkins_confirmed.loc[coord, 'Max_Date'].loc['data'] = max_date
    except Exception as e:
        print(e)
print('Lybia and malta were removed as they had NaN values')

Lybia and malta were removed as they had NaN values


In [130]:
hopkins_confirmed.iloc[:,12:].loc[coords[100]].loc['data'].max()

138.0

In [132]:
# sorted(hopkins_confirmed['Max_Cases'][::5])
len([a for a in hopkins_confirmed['Max_Cases'][::5] if a<20])
# hopkins_confirmed.loc[(67.04919196, -159.7503946)].iloc[:,12:]

0

In [95]:
hopkins_confirmed

Province_State  \
coordinate           information                                 
(-51.7963, -59.5236) data          Falkland Islands (Malvinas)   
                     avg_d_RH                              NaN   
                     avg_d_precip                          NaN   
                     avg_d_tmp                             NaN   
                     avg_d_wind                            NaN   
...                                                        ...   
(71.7069, -42.6043)  data                            Greenland   
                     avg_d_RH                              NaN   
                     avg_d_precip                          NaN   
                     avg_d_tmp                             NaN   
                     avg_d_wind                            NaN   

                                   Country_Region  avg_m_tmp   avg_m_RH  \
coordinate           information                                          
(-51.7963, -59.5236) data          United Kingdom  10.015094  77.632075   
                     avg_d_RH                 NaN        NaN        NaN   
                     avg_d_precip             NaN        NaN        NaN   
                     avg_d_tmp                NaN        NaN        NaN   
                     avg_d_wind               NaN        NaN        NaN   
...                                           ...        ...        ...   
(71.7069, -42.6043)  data                 Denmark -10.977358  61.490566   
                     avg_d_RH                 NaN        NaN        NaN   
                     avg_d_precip             NaN        NaN        NaN   
                     avg_d_tmp                NaN        NaN        NaN   
                     avg_d_wind               NaN        NaN        NaN   

                                   avg_m_precip  avg_m_wind  Max_Cases  \
coordinate           information                                         
(-51.7963, -59.5236) data                   0.0   29.204717       13.0   
                     avg_d_RH               NaN         NaN        NaN   
                     avg_d_precip           NaN         NaN        NaN   
                     avg_d_tmp              NaN         NaN        NaN   
                     avg_d_wind             NaN         NaN        NaN   
...                                         ...         ...        ...   
(71.7069, -42.6043)  data                   0.0   16.260377       11.0   
                     avg_d_RH               NaN         NaN        NaN   
                     avg_d_precip           NaN         NaN        NaN   
                     avg_d_tmp              NaN         NaN        NaN   
                     avg_d_wind             NaN         NaN        NaN   

                                    Max_Date 5%_Date  GF_Q1  ...  4/27/2020  \
coordinate           information                             ...              
(-51.7963, -59.5236) data          4/24/2020            NaN  ...       13.0   
                     avg_d_RH                           NaN  ...       83.0   
                     avg_d_precip                       NaN  ...        0.0   
                     avg_d_tmp                          NaN  ...        9.1   
                     avg_d_wind                         NaN  ...       26.1   
...                                      ...     ...    ...  ...        ...   
(71.7069, -42.6043)  data           4/4/2020            NaN  ...       11.0   
                     avg_d_RH                           NaN  ...       64.0   
                     avg_d_precip                       NaN  ...        0.0   
                     avg_d_tmp                          NaN  ...        3.0   
                     avg_d_wind                         NaN  ...       20.2   

                                   4/28/2020  4/29/2020  4/30/2020  5/1/2020  \
coordinate           information                                               
(-51.7963, -59.5236) data               13.0       13.0       

In [93]:
hopkins_confirmed.iloc[:,12:].loc[coords[10]].loc['data'].argmax() 
hopkins_confirmed.columns[117]

101

'5/6/2020'

##### Discard all locations where count < 20, add interval weather data - this should be done after comupting GF and 5% date

In [ ]:
coords = set(hopkins_confirmed.index.get_level_values(0).tolist())
discarded = 0
for coord in coords:
    cases = hopkins_confirmed.loc[coord]['Max_Cases']['data']
    if cases < 20:
        discarded += 1
        country = hopkins_confirmed.loc[coord]['Country_Region']['data']
        province = hopkins_confirmed.loc[coord]['Province_State']['data']
        print('Dropped {0}, {1}, {2} with {3} cases'.format(discarded, province, country, cases))
        hopkins_confirmed.drop(coord, level=0, inplace=True)
        continue
    try:
        last_rel_date = hopkins_confirmed.loc[coord]['last relevant date']['data']
        five_prcnt_date = hopkins_confirmed.loc[coord]['5%_Date']['data']

        five_prct_column = hopkins_confirmed.columns.get_loc(five_prcnt_date)
        last_rel_column = hopkins_confirmed.columns.get_loc(last_rel_date)
        interval = hopkins_confirmed[hopkins_confirmed.columns[five_prct_column:last_rel_column]]

        hopkins_confirmed.loc[coord, 'avg_interval_tmp']['data'] = interval.loc[coord].loc['avg_d_tmp'].mean(skipna=True)
        hopkins_confirmed.loc[coord, 'avg_interval_RH']['data'] = interval.loc[coord].loc['avg_d_RH'].mean(skipna=True)
    except KeyError as e:
        print('key error, {0}'.format(coord))

###### Sanity checks
Manual heuristic comparison of selected samples from the dataset
We compared 5 randomly selected data entries as follows:
1. lat and lan on google map
2. Daily information with Aeris API
3. Daily information with a third party climate source - https://www.worldweatheronline.com/
4. monthly information with a third party data source (This will only be an approximation) https://www.timeanddate.com/weather/israel/tel-aviv/climate
Note that coordinates are in decimal representation

We conclude that the data is correct heuristcially, except for precipitation that shows 0 when it is infact more in many cases
Also we see that except for US states coordinates are the same between Tableau and Hopkins datasets

In [646]:
# Israel 31\35
# All 4 check except precipitation
hopkins_confirmed.loc[(31,35)]
hopkins_confirmed.loc[(31,35)]['3/1/2020']

# # Afghanistan
# # All check
hopkins_confirmed.loc[(33,65)]
hopkins_confirmed.loc[(33,65)]['3/21/2020']

# # Queensland Australia
# # All check except precipitation
hopkins_confirmed.loc[(-28.0167,153.4)]
hopkins_confirmed.loc[(-28.0167,153.4)]['3/2/2020']

# Fiji
# All check except precipitation
hopkins_confirmed.loc[(-17.7134, 178.065)]
hopkins_confirmed.loc[(-17.7134, 178.065)]['3/6/2020']

Province_State Country_Region  avg_m_tmp   avg_m_RH  \
information                                                        
data                    NaN         Israel  14.721569  73.941176   
avg_d_RH                NaN            NaN        NaN        NaN   
avg_d_precip            NaN            NaN        NaN        NaN   
avg_d_tmp               NaN            NaN        NaN        NaN   
avg_d_wind              NaN            NaN        NaN        NaN   

              avg_m_precip  avg_m_wind  Max_Cases   Max_Date 5%_Date  GF_Q1  \
information                                                                   
data                   0.0   12.321569     3035.0  3/27/2020            NaN   
avg_d_RH               NaN         NaN        NaN                       NaN   
avg_d_precip           NaN         NaN        NaN                       NaN   
avg_d_tmp              NaN         NaN        NaN                       NaN   
avg_d_wind             NaN         NaN        NaN                       NaN   

                ...      3/18/2020  3/19/2020  3/20/2020  3/21/2020  \
information     ...                                                   
data            ...          304.0      427.0      529.0      712.0   
avg_d_RH        ...           64.0       70.0       81.0       76.0   
avg_d_precip    ...            0.0        0.0        0.0        0.0   
avg_d_tmp       ...           14.3       13.6       11.0       11.6   
avg_d_wind      ...           22.4       24.7       17.0       11.7   

              3/22/2020  3/23/2020  3/24/2020  3/25/2020  3/26/2020  3/27/2020  
information                                                                     
data              883.0     1071.0     1238.0     2369.0     2693.0     3035.0  
avg_d_RH           69.0       52.0       64.0       73.0       63.0       60.0  
avg_d_precip        0.0        0.0        0.0        0.0        0.0        0.0  
avg_d_tmp          13.6       18.2       18.2       16.4       18.1       20.7  
avg_d_wind          9.5        6.1       14.9        9.5        8.1       13.0  

[5 rows x 78 columns]

information
data            10.0
avg_d_RH        68.0
avg_d_precip     0.0
avg_d_tmp       15.3
avg_d_wind      23.0
Name: 3/1/2020, dtype: float64

Province_State Country_Region  avg_m_tmp   avg_m_RH  \
information                                                        
data                    NaN    Afghanistan  11.457576  51.924242   
avg_d_RH                NaN            NaN        NaN        NaN   
avg_d_precip            NaN            NaN        NaN        NaN   
avg_d_tmp               NaN            NaN        NaN        NaN   
avg_d_wind              NaN            NaN        NaN        NaN   

              avg_m_precip  avg_m_wind  Max_Cases   Max_Date 5%_Date  GF_Q1  \
information                                                                   
data              1.462424         8.6      110.0  3/27/2020            NaN   
avg_d_RH               NaN         NaN        NaN                       NaN   
avg_d_precip           NaN         NaN        NaN                       NaN   
avg_d_tmp              NaN         NaN        NaN                       NaN   
avg_d_wind             NaN         NaN        NaN                       NaN   

                ...      3/18/2020  3/19/2020  3/20/2020  3/21/2020  \
information     ...                                                   
data            ...           22.0       22.0       24.0       24.0   
avg_d_RH        ...           45.0       40.0       39.0       41.0   
avg_d_precip    ...            0.0        0.0        0.0        0.0   
avg_d_tmp       ...           18.0       19.3       19.6       18.7   
avg_d_wind      ...            1.9        2.7        4.8        2.4   

              3/22/2020  3/23/2020  3/24/2020  3/25/2020  3/26/2020  3/27/2020  
information                                                                     
data               40.0      40.00       74.0       84.0       94.0      110.0  
avg_d_RH           58.0      79.00       64.0       57.0       51.0       52.0  
avg_d_precip       12.7       7.62        0.0        0.0        0.0        0.0  
avg_d_tmp          17.8      16.10       14.4       15.2       16.7       16.1  
avg_d_wind         19.2       8.50        8.0        3.0        1.2       11.3  

[5 rows x 78 columns]

information
data            24.0
avg_d_RH        41.0
avg_d_precip     0.0
avg_d_tmp       18.7
avg_d_wind       2.4
Name: 3/21/2020, dtype: float64

Province_State Country_Region  avg_m_tmp   avg_m_RH  \
information                                                        
data             Queensland      Australia  24.078788  78.863636   
avg_d_RH                NaN            NaN        NaN        NaN   
avg_d_precip            NaN            NaN        NaN        NaN   
avg_d_tmp               NaN            NaN        NaN        NaN   
avg_d_wind              NaN            NaN        NaN        NaN   

              avg_m_precip  avg_m_wind  Max_Cases   Max_Date 5%_Date  GF_Q1  \
information                                                                   
data                   0.0   15.828788      555.0  3/27/2020            NaN   
avg_d_RH               NaN         NaN        NaN                       NaN   
avg_d_precip           NaN         NaN        NaN                       NaN   
avg_d_tmp              NaN         NaN        NaN                       NaN   
avg_d_wind             NaN         NaN        NaN                       NaN   

                ...      3/18/2020  3/19/2020  3/20/2020  3/21/2020  \
information     ...                                                   
data            ...           94.0      144.0      184.0      221.0   
avg_d_RH        ...           62.0       69.0       74.0       70.0   
avg_d_precip    ...            0.0        0.0        0.0        0.0   
avg_d_tmp       ...           22.0       21.7       22.4       24.5   
avg_d_wind      ...           20.1       10.0       13.9       16.6   

              3/22/2020  3/23/2020  3/24/2020  3/25/2020  3/26/2020  3/27/2020  
information                                                                     
data              259.0      319.0      397.0      443.0      493.0      555.0  
avg_d_RH           73.0       81.0       84.0       76.0       76.0       86.0  
avg_d_precip        0.0        0.0        0.0        0.0        0.0        0.0  
avg_d_tmp          25.0       23.2       20.9       21.9       22.1       20.0  
avg_d_wind         13.7       17.3       11.8       10.4       11.0       16.0  

[5 rows x 78 columns]

information
data             9.0
avg_d_RH        78.0
avg_d_precip     0.0
avg_d_tmp       25.6
avg_d_wind      12.8
Name: 3/2/2020, dtype: float64

Province_State Country_Region  avg_m_tmp   avg_m_RH  \
information                                                        
data                    NaN           Fiji  27.039394  84.954545   
avg_d_RH                NaN            NaN        NaN        NaN   
avg_d_precip            NaN            NaN        NaN        NaN   
avg_d_tmp               NaN            NaN        NaN        NaN   
avg_d_wind              NaN            NaN        NaN        NaN   

              avg_m_precip  avg_m_wind  Max_Cases   Max_Date 5%_Date  GF_Q1  \
information                                                                   
data                   0.0    6.854545        5.0  3/25/2020            NaN   
avg_d_RH               NaN         NaN        NaN                       NaN   
avg_d_precip           NaN         NaN        NaN                       NaN   
avg_d_tmp              NaN         NaN        NaN                       NaN   
avg_d_wind             NaN         NaN        NaN                       NaN   

                ...      3/18/2020  3/19/2020  3/20/2020  3/21/2020  \
information     ...                                                   
data            ...            0.0        1.0        1.0        1.0   
avg_d_RH        ...           92.0       97.0       94.0       91.0   
avg_d_precip    ...            0.0        0.0        0.0        0.0   
avg_d_tmp       ...           26.2       25.5       25.8       25.6   
avg_d_wind      ...            0.8        7.0        4.7        5.1   

              3/22/2020  3/23/2020  3/24/2020  3/25/2020  3/26/2020  3/27/2020  
information                                                                     
data                2.0        3.0        4.0        5.0        5.0        5.0  
avg_d_RH           89.0       91.0       87.0       86.0       85.0       87.0  
avg_d_precip        0.0        0.0        0.0        0.0        0.0        0.0  
avg_d_tmp          25.8       25.8       26.5       26.7       26.9       26.8  
avg_d_wind          1.7        4.7        4.9        5.5        5.0        4.8  

[5 rows x 78 columns]

information
data             0.0
avg_d_RH        90.0
avg_d_precip     0.0
avg_d_tmp       26.6
avg_d_wind       3.2
Name: 3/6/2020, dtype: float64

In [ ]:
data = pd.read_csv('../augmented_datasets/tableau_conf_data.csv')
RADIUS = 350

coords = [(31, 35), (33, 65), (-28.0167, 153.4), (-17.7134, 178.065), (47.5289, -99.784)] 
dates = ['03/01/2020', '03/21/2020', '03/02/2020', '03/06/2020', '03/12/2020']

for i in range(5):
    lat = coords[i][0]
    long = coords[i][1]
    start_time = dates[i]
    end_time = dates[i]
    location = data.loc[data['Lat'] == lat]\
                    .loc[data['Long'] == long]\
                     [['Country_Region','Province_State']]
    country = location.iloc[0][0]
    province = location.iloc[0][1]
    url = 'https://api.aerisapi.com/observations/summary/closest?p={0},{1}&from={2}&to={3}&radius={4}miles&plimit=31&limit=1&'\
          'client_id={5}&client_secret={6}'.format(lat, long, start_time, end_time, RADIUS, client_id, client_secret)
    print('collecting for {0} location {1}, {2}\n{3}'.format(i, province, country, url))
    request = urllib.request.urlopen(url)
    response = request.read()
    json_ = json.loads(response)
    if json_['success']: 
        print('success')
        try:
            for day in json_['response'][0]['periods']:
                print('Location: {0}, {1}'.format(json_['response'][0]['place']['name'], json_['response'][0]['place']['city']))
                print('avg tmp: {0}'.format(day['summary']['temp']['avgC']))
                print('avg RH: {0}'.format(day['summary']['rh']['avg']))
                print('avg wind: {0}'.format(day['summary']['wind']['avgKPH']))
                print('avg precip: {0}\n'.format(day['summary']['precip']['totalMM']))
        except IndexError:
            if json_['error']:
                msg = 'No data found for {0}, {1} at {2}\n{3}\r\n'.format(country, province, date, json_['error'])
                print(msg)
        except Exception as e:
            raise e
            msg = 'Unknowen error\n{0}\r\n'.format(json_['error'])
            print(msg)
        finally:
            request.close()



- Israel, 03/01/20, 31	35	15.3	68	23	0	14.99310345	74.5862069	13.11034483	0
    * Google maps
    * Check API
    * Third party daily
    * Third party monthly
- Afghanistan, 03/21/20 33	65	18.7	41	2.4	0	13.71315789	47.07894737	5.684210526	0.855526316
    * Google maps
    * Check API
    * Third party daily
    * Third party monthly

- Queensland Australia, 02/03/20 -28.0167	153.4	25.6	78	12.8	0	24.05	75.55263158	16.66842105	0
    * Google maps
    * Check API
    * Third party daily
    * Third party monthly

- Fiji, 03/06/20 -17.7134	178.065	26.6	90	3.2	0	26.84473684	85.47368421	5.871052632	0
    * Google maps
        - The the northen third of Fiji
    * Check API
        - Checks good for Nausori (60km south east)
    * Third party daily
        - Checks good exepct wind that seems week and precipitation that should be a little
    * Third party monthly
        - seems good exepct for precipitation
- North Dakota, US 03/12/20 47.5289	-99.784	-0.2	73	31.5	0	-4.947368421	80.52631579	18.72368421	0
    * Google maps
        - In the fields around the middle of the state
    * Check API
         - Checks good for harvey (10km north west)
    * Third party daily
        - 
    * Third party monthly
        - checks good except precipitation

After comparing the data we conclude it is relaibale except for precpitation that will be hence forth ignored.

###### Add 5% interval and averages + reloading a saved pickle

In [51]:
# DONT RUN THIS BOX IF YOU RAN THE SCRIPT FROM THE START
hopkins_confirmed = pd.DataFrame()
PICKLE_PATH = '../augmented_datasets/hopkins_conf_augmented2903.pkl'
with open(PICKLE_PATH, 'rb') as file:
    hopkins_confirmed = pickle.load(file)
coords = set(hopkins_confirmed.index.get_level_values(0).tolist())

In [285]:
hopkins_confirmed.insert(9, 'avg_interval_RH', np.nan)
hopkins_confirmed.insert(9, 'avg_interval_tmp', np.nan)

In [144]:
for coord in coords:
    max_cases = int(hopkins_confirmed.loc[coord]['Max_Cases']['data'])
    max_date = hopkins_confirmed.loc[coord]['Max_Date']
    five_prcnt = int(0.05 * max_cases)
    mask = hopkins_confirmed.loc[coord].loc['data'][14:] >= five_prcnt
    five_prcnt_date = mask.index.min()
    hopkins_confirmed.loc[coord, '5%_Date']['data'] = five_prcnt_date
    
    five_prct_column = hopkins_confirmed.columns.get_loc(five_prcnt_date)
    max_column = hopkins_confirmed.columns.get_loc(max_date['data'])
    interval = hopkins_confirmed[hopkins_confirmed.columns[five_prct_column:max_column]]
    
    hopkins_confirmed.loc[coord, 'avg_interval_tmp']['data'] = interval.loc[coord].loc['avg_d_tmp'].mean(skipna=True)
    hopkins_confirmed.loc[coord, 'avg_interval_RH']['data'] = interval.loc[coord].loc['avg_d_RH'].mean(skipna=True)

###### Save augmented data
1. Multi index does not save well in csv, so we also save it as a pickle

In [297]:
pickle_path = '../augmented_datasets/pickles/hopkins_conf_augmented{0}.pkl'.format(datetime.now().strftime('%d%m'))
with open(pickle_path, 'wb') as file:
    pickle.dump(hopkins_confirmed, file)
hopkins_confirmed.to_csv('../augmented_datasets/hopkins_conf_augmented{0}.csv'.format(datetime.now().strftime('%d%m')))